In [3]:
import sympy as sym

def cubic_spline_clamped(xs: list[float],
                         ys: list[float],
                         B0: float,
                         B1: float
                        ) -> list[sym.Expr]:
    """
    Interpolación por splines cúbicos condicionados (clamped).
    
    Parámetros:
    - xs, ys: listas de abscisas y ordenadas de los puntos (no tienen que estar ordenadas).
    - B0: pendiente deseada en x0, es decir S'(x0) = B0.
    - B1: pendiente deseada en xn, es decir S'(xn) = B1.
    
    Devuelve:
    - Lista de n polinomios sympy S_j(x) que interpolan en los intervalos [x_j, x_{j+1}].
    """
    # 1) Ordenar los puntos por la coordenada x
    puntos = sorted(zip(xs, ys), key=lambda p: p[0])
    xs = [p[0] for p in puntos]
    ys = [p[1] for p in puntos]
    n = len(xs) - 1
    
    # 2) Calcular longitudes de intervalos h_i
    h = [xs[i+1] - xs[i] for i in range(n)]
    
    # 3) Construir el vector alpha con las condiciones en los extremos
    alpha = [0.0]*(n+1)
    # extremo izquierdo (clamped en B0):
    alpha[0] = 3*(ys[1] - ys[0]) / h[0] - 3*B0
    # interior:
    for i in range(1, n):
        alpha[i] = (3/h[i])*(ys[i+1] - ys[i]) \
                 - (3/h[i-1])*(ys[i] - ys[i-1])
    # extremo derecho (clamped en B1):
    alpha[n] = 3*B1 - 3*(ys[n] - ys[n-1]) / h[n-1]
    
    # 4) Thomas (descomposición tridiagonal)
    l = [1.0]
    mu = [0.0]
    z = [0.0]
    for i in range(1, n):
        li = 2*(xs[i+1] - xs[i-1]) - h[i-1]*mu[i-1]
        l.append(li)
        mu.append(h[i] / li)
        zi = (alpha[i] - h[i-1]*z[i-1]) / li
        z.append(zi)
    l.append(1.0)
    z.append(0.0)
    
    # 5) Back-substitution para c_j
    c = [0.0]*(n+1)
    for j in range(n-1, -1, -1):
        c[j] = z[j] - mu[j]*c[j+1]
    
    # 6) Calcular a, b, d y construir S_j(x)
    x = sym.Symbol('x')
    splines = []
    for j in range(n):
        a = ys[j]
        b = (ys[j+1] - ys[j]) / h[j] \
            - (h[j]/3)*(2*c[j] + c[j+1])
        d = (c[j+1] - c[j]) / (3*h[j])
        # Polinomio simbólico:
        Sj = sym.simplify(
            a
            + b*(x - xs[j])
            + c[j]*(x - xs[j])**2
            + d*(x - xs[j])**3
        )
        splines.append(Sj)
    
    return splines

In [4]:
xs = [0, 1, 2]
ys = [1, 5, 3]

splines = cubic_spline(xs=xs, ys=ys)
_ = [display(s) for s in splines]
print("______")
_ = [display(s.expand()) for s in splines]

-1.5*x**3 + 5.5*x + 1

1.5*x**3 - 9.0*x**2 + 14.5*x - 2.0

______


-1.5*x**3 + 5.5*x + 1

1.5*x**3 - 9.0*x**2 + 14.5*x - 2.0

In [5]:
xs = [0, 1, 2]
ys = [-5, -4, 3]

splines = cubic_spline(xs=xs, ys=ys)
_ = [display(s) for s in splines]
print("______")
_ = [display(s.expand()) for s in splines]

1.5*x**3 - 0.5*x - 5

-1.5*x**3 + 9.0*x**2 - 9.5*x - 2.0

______


1.5*x**3 - 0.5*x - 5

-1.5*x**3 + 9.0*x**2 - 9.5*x - 2.0

In [6]:
xs = [0, 1, 2,3]
ys = [1, 1, 5,2]

splines = cubic_spline(xs=xs, ys=ys)
_ = [display(s) for s in splines]
print("______")
_ = [display(s.expand()) for s in splines]

1.53333333333333*x**3 - 1.53333333333333*x + 1

-3.66666666666667*x**3 + 15.6*x**2 - 17.1333333333333*x + 6.2

2.13333333333333*x**3 - 19.2*x**2 + 52.4666666666667*x - 40.2

______


1.53333333333333*x**3 - 1.53333333333333*x + 1

-3.66666666666667*x**3 + 15.6*x**2 - 17.1333333333333*x + 6.2

2.13333333333333*x**3 - 19.2*x**2 + 52.4666666666667*x - 40.2

In [19]:
import numpy as np
import sympy as sp
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

def cubic_spline_clamped(xs, ys, B0, B1):
    # 1) Ordenar puntos
    puntos = sorted(zip(xs, ys), key=lambda p: p[0])
    xs = [p[0] for p in puntos]
    ys = [p[1] for p in puntos]
    n = len(xs) - 1

    # 2) Longitudes de intervalos
    h = [xs[i+1] - xs[i] for i in range(n)]

    # 3) Vector alpha con condiciones en extremos
    alpha = [0.0]*(n+1)
    alpha[0] = 3*(ys[1] - ys[0]) / h[0] - 3*B0
    for i in range(1, n):
        alpha[i] = (3/h[i])*(ys[i+1] - ys[i]) \
                 - (3/h[i-1])*(ys[i] - ys[i-1])
    alpha[n] = 3*B1 - 3*(ys[n] - ys[n-1]) / h[n-1]

    # 4) Thomas para sistema tridiagonal
    l = [1.0]; mu = [0.0]; z = [0.0]
    for i in range(1, n):
        li = 2*(xs[i+1] - xs[i-1]) - h[i-1]*mu[i-1]
        l.append(li)
        mu.append(h[i] / li)
        z.append((alpha[i] - h[i-1]*z[i-1]) / li)
    l.append(1.0); z.append(0.0)

    # 5) Back-substitute para c
    c = [0.0]*(n+1)
    for j in range(n-1, -1, -1):
        c[j] = z[j] - mu[j]*c[j+1]

    # 6) Coeficientes b, d y lambdify de cada tramo
    b = []; d = []
    x = sp.symbols('x')
    spl_funcs = []
    for j in range(n):
        a_j = ys[j]
        b_j = (ys[j+1] - ys[j]) / h[j] - (h[j]/3)*(2*c[j] + c[j+1])
        d_j = (c[j+1] - c[j]) / (3*h[j])
        b.append(b_j); d.append(d_j)
        Sj = a_j + b_j*(x - xs[j]) + c[j]*(x - xs[j])**2 + d_j*(x - xs[j])**3
        spl_funcs.append(sp.lambdify(x, Sj, 'numpy'))

    return spl_funcs, b, c, d

# Parámetros y figura
xs = [0, 1, 2]
ys = [1, 5, 3]
B0 = 1.0  # pendiente en x0

fig, ax = plt.subplots()
# Extiende el eje X hasta 3
ax.set_xlim(xs[0], 3)
ax.set_ylim(min(ys) - 1, max(ys) + 1)

# Dibujar puntos y anotaciones
ax.scatter(xs, ys, color='red', zorder=5)
for xi, yi in zip(xs, ys):
    ax.annotate(f"({xi},{yi})", xy=(xi, yi),
                xytext=(5,5), textcoords='offset points',
                fontsize=9, color='darkred')

# Preparar colores distintos para cada spline
n_seg = len(xs) - 1
cmap = plt.get_cmap('tab10')
colors = [cmap(i) for i in range(n_seg)]

# Crear artistas para cada tramo
spl_lines = [
    ax.plot([], [], lw=2, color=colors[i], label=f"Spline {i+1}")[0]
    for i in range(n_seg)
]

# Artista para la tangente y texto de pendiente
tangent_line, = ax.plot([], [], 'g--', lw=2, label="Tangente en x₂")
slope_text = ax.text(0.02, 0.95, '',
                     transform=ax.transAxes,
                     fontsize=10, color='green')

def init():
    for ln in spl_lines:
        ln.set_data([], [])
    tangent_line.set_data([], [])
    slope_text.set_text('')
    return spl_lines + [tangent_line, slope_text]

def update(B1):
    # Recalcular splines y coeficientes
    funcs, b, c, d = cubic_spline_clamped(xs, ys, B0, B1)
    h0 = xs[1] - xs[0]
    h1 = xs[2] - xs[1]

    # 1er tramo (clamped natural)
    x0 = np.linspace(xs[0], xs[1], 200)
    spl_lines[0].set_data(x0, funcs[0](x0))

    # Pendiente en x₁ para Hermite
    m1 = b[0] + 2*c[0]*h0 + 3*d[0]*h0**2

    # 2º tramo (Hermite con pendiente interna m1 y externa B1)
    x1 = np.linspace(xs[1], xs[2], 200)
    t  = (x1 - xs[1]) / h1
    h00 =  2*t**3 - 3*t**2 + 1
    h10 =    t**3 - 2*t**2 + t
    h01 = -2*t**3 + 3*t**2
    h11 =    t**3 -   t**2
    y1_hermite = (h00*ys[1] +
                  h10*m1*h1 +
                  h01*ys[2] +
                  h11*B1*h1)
    spl_lines[1].set_data(x1, y1_hermite)

    # Dibujar recta tangente en x₂
    x2, y2 = xs[-1], ys[-1]
    xt = np.linspace(x2-0.5, x2+0.5, 100)
    yt = y2 + B1*(xt - x2)
    tangent_line.set_data(xt, yt)

    # Actualizar texto de pendiente
    slope_text.set_text(f"S'(x₂) = {B1:.3f}")
    ax.set_title("Cada spline con color distinto y eje X hasta 3")
    return spl_lines + [tangent_line, slope_text]

# Crear animación
B1_vals = np.linspace(-3, 3, 61)
anim = FuncAnimation(fig, update, frames=B1_vals,
                     init_func=init, blit=True, interval=200)

ax.legend(loc='upper right')
plt.close(fig)  # Evita mostrar figura estática en notebooks
HTML(anim.to_jshtml())


In [20]:
import numpy as np
import sympy as sp
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

def cubic_spline_clamped(xs, ys, B0, B1):
    # 1) Ordenar puntos
    puntos = sorted(zip(xs, ys), key=lambda p: p[0])
    xs = [p[0] for p in puntos]
    ys = [p[1] for p in puntos]
    n = len(xs) - 1

    # 2) Longitudes de intervalos
    h = [xs[i+1] - xs[i] for i in range(n)]

    # 3) Vector alpha con condiciones en extremos
    alpha = [0.0]*(n+1)
    alpha[0] = 3*(ys[1] - ys[0]) / h[0] - 3*B0
    for i in range(1, n):
        alpha[i] = (3/h[i])*(ys[i+1] - ys[i]) \
                 - (3/h[i-1])*(ys[i] - ys[i-1])
    alpha[n] = 3*B1 - 3*(ys[n] - ys[n-1]) / h[n-1]

    # 4) Thomas para sistema tridiagonal
    l = [1.0]; mu = [0.0]; z = [0.0]
    for i in range(1, n):
        li = 2*(xs[i+1] - xs[i-1]) - h[i-1]*mu[i-1]
        l.append(li)
        mu.append(h[i] / li)
        z.append((alpha[i] - h[i-1]*z[i-1]) / li)
    l.append(1.0); z.append(0.0)

    # 5) Back-substitute para c
    c = [0.0]*(n+1)
    for j in range(n-1, -1, -1):
        c[j] = z[j] - mu[j]*c[j+1]

    # 6) Coeficientes b, d y lambdify de cada tramo
    b = []; d = []
    x = sp.symbols('x')
    spl_funcs = []
    for j in range(n):
        a_j = ys[j]
        b_j = (ys[j+1] - ys[j]) / h[j] - (h[j]/3)*(2*c[j] + c[j+1])
        d_j = (c[j+1] - c[j]) / (3*h[j])
        b.append(b_j); d.append(d_j)
        Sj = a_j + b_j*(x - xs[j]) + c[j]*(x - xs[j])**2 + d_j*(x - xs[j])**3
        spl_funcs.append(sp.lambdify(x, Sj, 'numpy'))

    return spl_funcs, b, c, d

# Parámetros y figura
xs = [0, 1, 2]
ys = [-5, -4, 3]
B0 = 1.0  # pendiente en x0

fig, ax = plt.subplots()
# Extiende el eje X hasta 3
ax.set_xlim(xs[0], 3)
ax.set_ylim(min(ys) - 1, max(ys) + 1)

# Dibujar puntos y anotaciones
ax.scatter(xs, ys, color='red', zorder=5)
for xi, yi in zip(xs, ys):
    ax.annotate(f"({xi},{yi})", xy=(xi, yi),
                xytext=(5,5), textcoords='offset points',
                fontsize=9, color='darkred')

# Preparar colores distintos para cada spline
n_seg = len(xs) - 1
cmap = plt.get_cmap('tab10')
colors = [cmap(i) for i in range(n_seg)]

# Crear artistas para cada tramo
spl_lines = [
    ax.plot([], [], lw=2, color=colors[i], label=f"Spline {i+1}")[0]
    for i in range(n_seg)
]

# Artista para la tangente y texto de pendiente
tangent_line, = ax.plot([], [], 'g--', lw=2, label="Tangente en x₂")
slope_text = ax.text(0.02, 0.95, '',
                     transform=ax.transAxes,
                     fontsize=10, color='green')

def init():
    for ln in spl_lines:
        ln.set_data([], [])
    tangent_line.set_data([], [])
    slope_text.set_text('')
    return spl_lines + [tangent_line, slope_text]

def update(B1):
    # Recalcular splines y coeficientes
    funcs, b, c, d = cubic_spline_clamped(xs, ys, B0, B1)
    h0 = xs[1] - xs[0]
    h1 = xs[2] - xs[1]

    # 1er tramo (clamped natural)
    x0 = np.linspace(xs[0], xs[1], 200)
    spl_lines[0].set_data(x0, funcs[0](x0))

    # Pendiente en x₁ para Hermite
    m1 = b[0] + 2*c[0]*h0 + 3*d[0]*h0**2

    # 2º tramo (Hermite con pendiente interna m1 y externa B1)
    x1 = np.linspace(xs[1], xs[2], 200)
    t  = (x1 - xs[1]) / h1
    h00 =  2*t**3 - 3*t**2 + 1
    h10 =    t**3 - 2*t**2 + t
    h01 = -2*t**3 + 3*t**2
    h11 =    t**3 -   t**2
    y1_hermite = (h00*ys[1] +
                  h10*m1*h1 +
                  h01*ys[2] +
                  h11*B1*h1)
    spl_lines[1].set_data(x1, y1_hermite)

    # Dibujar recta tangente en x₂
    x2, y2 = xs[-1], ys[-1]
    xt = np.linspace(x2-0.5, x2+0.5, 100)
    yt = y2 + B1*(xt - x2)
    tangent_line.set_data(xt, yt)

    # Actualizar texto de pendiente
    slope_text.set_text(f"S'(x₂) = {B1:.3f}")
    ax.set_title("Cada spline con color distinto y eje X hasta 3")
    return spl_lines + [tangent_line, slope_text]

# Crear animación
B1_vals = np.linspace(-3, 3, 61)
anim = FuncAnimation(fig, update, frames=B1_vals,
                     init_func=init, blit=True, interval=200)

ax.legend(loc='upper right')
plt.close(fig)  # Evita mostrar figura estática en notebooks
HTML(anim.to_jshtml())


In [27]:
import numpy as np
import sympy as sp
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

def cubic_spline_clamped(xs, ys, B0, B1):
    # 1) Ordenar puntos
    puntos = sorted(zip(xs, ys), key=lambda p: p[0])
    xs = [p[0] for p in puntos]
    ys = [p[1] for p in puntos]
    n = len(xs) - 1

    # 2) Longitudes de intervalos
    h = [xs[i+1] - xs[i] for i in range(n)]

    # 3) Vector alpha con condiciones en extremos
    alpha = [0.0]*(n+1)
    alpha[0]   = 3*(ys[1]  - ys[0])   / h[0]   - 3*B0
    for i in range(1, n):
        alpha[i] = (3/h[i])*(ys[i+1] - ys[i]) - (3/h[i-1])*(ys[i] - ys[i-1])
    alpha[n]   = 3*B1 - 3*(ys[n] - ys[n-1]) / h[n-1]

    # 4) Thomas para sistema tridiagonal
    l = [1.0]; mu = [0.0]; z = [0.0]
    for i in range(1, n):
        li = 2*(xs[i+1] - xs[i-1]) - h[i-1]*mu[i-1]
        l.append(li)
        mu.append(h[i]/li)
        z.append((alpha[i] - h[i-1]*z[i-1]) / li)
    l.append(1.0); z.append(0.0)

    # 5) Back-substitute para c
    c = [0.0]*(n+1)
    for j in range(n-1, -1, -1):
        c[j] = z[j] - mu[j]*c[j+1]

    # 6) Coeficientes b, d y lambdify de cada tramo
    b = []; d = []
    x = sp.symbols('x')
    funcs = []
    for j in range(n):
        a_j = ys[j]
        b_j = (ys[j+1] - ys[j]) / h[j] - (h[j]/3)*(2*c[j] + c[j+1])
        d_j = (c[j+1] - c[j]) / (3*h[j])
        b.append(b_j); d.append(d_j)
        Sj = a_j + b_j*(x - xs[j]) + c[j]*(x - xs[j])**2 + d_j*(x - xs[j])**3
        funcs.append(sp.lambdify(x, Sj, 'numpy'))
    return funcs, b, c, d

# ——————————————————————————————————————————————————————————
# Parámetros y figura
xs = [0, 1, 2, 3]
ys = [-1, 1, 5, 2]
B0 = 1.0  # pendiente en x0

fig, ax = plt.subplots()
ax.set_xlim(xs[0], 5)
ax.set_ylim(min(ys)-1, max(ys)+1)

# Dibujar puntos y anotaciones
ax.scatter(xs, ys, color='red', zorder=5)
for xi, yi in zip(xs, ys):
    ax.annotate(f"({xi},{yi})", xy=(xi, yi),
                xytext=(5,5), textcoords='offset points',
                fontsize=9, color='darkred')

# Colores para cada spline
n_seg = len(xs) - 1
cmap = plt.get_cmap('tab10')
colors = [cmap(i) for i in range(n_seg)]

# Crear artista por tramo
spl_lines = [
    ax.plot([], [], lw=2, color=colors[i], label=f"Spline {i+1}")[0]
    for i in range(n_seg)
]

# Tangente en el último punto y texto
tangent_line, = ax.plot([], [], 'g--', lw=2, label="Tangente en x₃")
slope_text = ax.text(0.02, 0.95, '', transform=ax.transAxes,
                     fontsize=10, color='brown')

def init():
    for ln in spl_lines:
        ln.set_data([], [])
    tangent_line.set_data([], [])
    slope_text.set_text('')
    return spl_lines + [tangent_line, slope_text]

def update(B1):
    funcs, b, c, d = cubic_spline_clamped(xs, ys, B0, B1)

    # 1er y 2º tramo: spline clamped estándar
    for j in [0, 1]:
        xj = np.linspace(xs[j], xs[j+1], 200)
        spl_lines[j].set_data(xj, funcs[j](xj))

    # 3er tramo: Hermite para garantizar pendiente B1 en x3
    j = 2
    h_prev = xs[j]   - xs[j-1]
    h_last = xs[j+1] - xs[j]
    # pendiente interna en x2
    m_in = b[j-1] + 2*c[j-1]*h_prev + 3*d[j-1]*h_prev**2

    x3 = np.linspace(xs[j], xs[j+1], 200)
    t  = (x3 - xs[j]) / h_last
    h00 =  2*t**3 - 3*t**2 + 1
    h10 =    t**3 - 2*t**2 + t
    h01 = -2*t**3 + 3*t**2
    h11 =    t**3 -   t**2
    y3 = (h00*ys[j] +
          h10*m_in*h_last +
          h01*ys[j+1] +
          h11*B1*h_last)
    spl_lines[j].set_data(x3, y3)

    # Dibujar la tangente en x3
    x3p, y3p = xs[-1], ys[-1]
    xt = np.linspace(x3p-0.5, x3p+0.5, 100)
    yt = y3p + B1*(xt - x3p)
    tangent_line.set_data(xt, yt)

    slope_text.set_text(f"S'(x₃) = {B1:.3f}")
    return spl_lines + [tangent_line, slope_text]

# Animación
B1_vals = np.linspace(-3, 3, 61)
anim = FuncAnimation(fig, update, frames=B1_vals,
                     init_func=init, blit=True, interval=200)

ax.legend(loc='upper right')
plt.close(fig)
HTML(anim.to_jshtml())
